# Домашнее задание № 10. Генерация текста

### Задание 1 (8 баллов).

Попробуйте дообучать GPT на каком-то другом тексте (можете попробовать любые стихи или какие-то специфичные вещи вроде анекдотов или репа). 
Попробуйте разные методы и параметры генерации (beam search, температура, top_k и тп). Сохраните в тетрадке несколько хороших сгенерированных текстов


#### Создание датасета русского репа

In [118]:
import requests
from bs4 import BeautifulSoup
import re

In [266]:
def extract_sentences(text):
    # Define a regular expression pattern to match sentences surrounded by newline characters with leading/trailing whitespace
    pattern = r'\n\s{10,}(.+)\n\s{10,}'
    # Use the re.findall function to find all matches
    sentences = re.findall(pattern, text, re.DOTALL)

    return sentences

In [267]:
dataset = {
    "rap" : {
        "artists" : {}
    }
}

In [268]:
def scrape_rap_text(url, name):
    pattern = r'/(\d+(-\d+)?)-'
    print(url)
    rap_page = requests.get(url)
    rap_soup = BeautifulSoup(rap_page.content, 'html.parser')
    try:
        div_class = f"news-id-{re.findall(pattern, url)[0][0]}"
    except:
        return
    # print(div_class)
    rap_div = rap_soup.find('div', id=div_class)
    try:
        rap_div.find('p')
    except:
        fix_pattern = r'/(\d+)-'
        div_class = f"news-id-{re.findall(fix_pattern, url)[0]}"
        rap_div = rap_soup.find('div', id=div_class)
    if rap_div.find('p'):
        rap_p = rap_div.find('p')
        for br in rap_p.find_all('br'):
            br.replace_with("\n")
        # print(rap_p.text)
        rap_text_list = [t.strip() for t in rap_p.text.split("\n")[1:]]
        rap = "\r\n".join(rap_text_list).strip()
        rap_name = rap_p.text.split("\n")[0].strip()
    else:
        # print(rap_div.text)
        rap_text_list = [t.strip() for t in rap_div.text.split("\r\n")[1:]]
        rap = "\r\n".join(rap_text_list).strip()
        rap_name = rap_div.text.split("\r\n")[0].strip()
    if len(rap) < 1:
        print("rap not found")
    else:
        dataset["rap"]["artists"][name][rap_name] = {"text" : rap, "link" : url}

In [269]:
def visit_artist(url, name):
    dataset["rap"]["artists"][name] = {}
    visit_page = requests.get(url)
    visit_soup = BeautifulSoup(visit_page.content, 'html.parser')
    visit_div = visit_soup.find('div', class_="nav nav-pills nav-stacked")
    for li in visit_div.find_all('li'):
        text_link = li.find('a', href=True)
        text_link = text_link['href']
        scrape_rap_text(text_link, name)

In [270]:
base_url = "https://rap-text.ru"
page = requests.get(base_url)
soup = BeautifulSoup(page.content, 'html.parser')

In [271]:
divs = soup.find_all('div', class_="col-md-5 artist_block")
artist_name_pattern = r'/(.+).html'
for div in divs:
    link = div.find('span').find('a', href=True)
    target_url = base_url + link['href']
    print(target_url)
    artist_name = re.findall(artist_name_pattern, link['href'])[0]
    print(artist_name)
    visit_artist(target_url, artist_name)

https://rap-text.ru/vitya_ak.html
vitya_ak
https://rap-text.ru/vitya_ak/1229-vitja-ak-common-tekst-pesni.html
https://rap-text.ru/vitya_ak/3479-vitja-ak-feat.-mc-bandit-happy-new-year.html
https://rap-text.ru/vitya_ak/3864-vitja-ak-hit-the-road-jack-tekst-pesni.html
https://rap-text.ru/vitya_ak/3881-vitja-ak-feat.-rynochnye-otnoshenija.html
https://rap-text.ru/vitya_ak/11151-vitya-ak-apokalipsis-tekst-pesni.html
https://rap-text.ru/vitya_ak/9742-vitya-ak-feat-tip-bednyy-mozhet-stat-bogatym-tekst-pesni.html
https://rap-text.ru/vitya_ak/4338-vitja-ak-feat.-mic-dog-vesennjaja-tekst.html
https://rap-text.ru/vitya_ak/9109-vitja-ak-feat.-praga13-vzlety-i.html
https://rap-text.ru/vitya_ak/10407-vitya-ak-vitin-krank-tekst-pesni.html
https://rap-text.ru/vitya_ak/3866-vitja-ak-vitja-ak-tekst-pesni.html
https://rap-text.ru/vitya_ak/3885-vitja-ak-feat.-khus-volosatyjj-arbuz.html
https://rap-text.ru/vitya_ak/11165-vitya-ak-vse-ms-tekst-pesni.html
https://rap-text.ru/vitya_ak/9628-vitya-ak-feat-tip-

In [272]:
dataset

{'rap': {'artists': {'vitya_ak': {'Витя АК - Common (текст песни)': {'text': 'Каждый кто АК слышал дважды\r\nСтанут узнавать в лицо в автобусе однажды\r\nИначе как же, я среди обычных граждан\r\nАК запомни не производит лажу\r\nЯ вот че скажу, это старая школа\r\nЖопа с пальцем, АК и Пугачева\r\nПо хуй что не так масштабно, ну и пусть\r\nНе держу обиды и не таю грусть\r\nКто сделал вид, что в рэпе индивид\r\nИз-за вас бошка болит, портит панорамы вид\r\nЧе там кто там с АК хотел тягаться\r\nВатакатство тоже дает в себе разобраться\r\nЯ не модный, подчеркните это\r\nЗакаляюся зимой, на Урале мало лета\r\nЗато много бита, много баса\r\nКатанных комков и просто ганджубаса\r\nКомммон, комммон твою мать\r\nКомммон, комммон твою мать\r\nКомммон, комммон, коммон, коммон\r\nЯ из тех кланов, я из тех квот\r\nНравиться мне, как на девятках труба орет\r\nЯ питаюсь быстро, дела мучу чисто\r\nВ армию не собираюсь, считаю это лишним\r\nНравятся блондинки, нравятся брюнетки\r\nТату на пояснице и редк

In [6]:
import json

In [274]:
with open('train_dataset.json', 'w', encoding='utf-8') as f:
    json.dump(dataset, f, ensure_ascii=False, indent=4)

#### Дообучение

In [1]:
%pip install transformers

Note: you may need to restart the kernel to use updated packages.


In [2]:
from transformers.utils import logging
logging.set_verbosity(40)

In [3]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer
import torch
DEVICE = torch.device("cuda:0")

In [4]:
model_name_or_path = "sberbank-ai/rugpt3small_based_on_gpt2"
tokenizer = GPT2Tokenizer.from_pretrained(model_name_or_path)
model = GPT2LMHeadModel.from_pretrained(model_name_or_path, use_cache=False).to(DEVICE)

In [5]:
from transformers import TextDataset, DataCollatorForLanguageModeling

In [8]:
with open("train_dataset.json", "r", encoding="UTF8") as f:
    dataset = json.load(f)

In [11]:
for artist in dataset['rap']['artists']:
    print(artist)

vitya_ak
guf
smoki_mo
kripl
dino_mc_47
kasta
basta
noize_mc
drago
karandash
gidroponka
loc_dog
tandem_foundation
st1m


In [18]:
text = ''''''
for artist in dataset['rap']['artists']:
    for rap_song in dataset['rap']['artists'][artist]:
        print(rap_song)
        text += dataset['rap']['artists'][artist][rap_song]['text'] + '\r\n\r\n\r\n'

Витя АК - Common (текст песни)
Витя АК feat. MC Bandit -  Happy New Year 2010 (текст песни)
Витя АК - Hit the road jack (текст песни)
Витя АК feat. Рыночные Отношения - Авитаминоз (текст песни)
Витя АК - Апокалипсис (текст песни)
Витя АК feat. Tip - Бедный может стать богатым (текст песни)
Витя АК feat. Mic Dog - Весенняя (текст песни)
Витя АК feat. Прага13 - Взлеты и падения (текст песни)
Витя АК - Витин кранк (текст песни)
Витя АК - Витя АК (текст песни)
Витя АК feat. Хус - Волосатый арбуз (текст песни)
Витя АК - Все МС (текст песни)
Витя АК feat. Tip - Все будет хорошо (текст песни)
Витя АК feat. MC Bandit, Notice - Всё обо всём (текст песни)
Витя АК feat. Аля Кумар - Все равно (текст песни)
Витя АК - В то время как (текст песни)
Витя АК feat. Tip - Грубо говоря (текст песни)
Витя АК feat. Avetis - Дай денег (текст песни)
Витя АК feat. Bugz - Дисс Ре (текст песни)
Витя АК feat. Восточный Округ - Закачались головы (текст песни)
Витя АК feat. Рыночные Отношения - Как хуй когда (текст 

In [19]:
text

'Каждый кто АК слышал дважды\r\nСтанут узнавать в лицо в автобусе однажды\r\nИначе как же, я среди обычных граждан\r\nАК запомни не производит лажу\r\nЯ вот че скажу, это старая школа\r\nЖопа с пальцем, АК и Пугачева\r\nПо хуй что не так масштабно, ну и пусть\r\nНе держу обиды и не таю грусть\r\nКто сделал вид, что в рэпе индивид\r\nИз-за вас бошка болит, портит панорамы вид\r\nЧе там кто там с АК хотел тягаться\r\nВатакатство тоже дает в себе разобраться\r\nЯ не модный, подчеркните это\r\nЗакаляюся зимой, на Урале мало лета\r\nЗато много бита, много баса\r\nКатанных комков и просто ганджубаса\r\nКомммон, комммон твою мать\r\nКомммон, комммон твою мать\r\nКомммон, комммон, коммон, коммон\r\nЯ из тех кланов, я из тех квот\r\nНравиться мне, как на девятках труба орет\r\nЯ питаюсь быстро, дела мучу чисто\r\nВ армию не собираюсь, считаю это лишним\r\nНравятся блондинки, нравятся брюнетки\r\nТату на пояснице и редкие пометки\r\nПацики мы меткие, опасны как коррозия\r\nЧто вечером курили, на

In [6]:
train_path = 'train_dataset.txt'

In [22]:
with open(train_path, "w", encoding="UTF8") as f:
    f.write(text)

In [7]:
# Создание датасета
train_dataset = TextDataset( tokenizer=tokenizer,file_path=train_path,block_size=64,
                            overwrite_cache=True)

# специальный класс который будет подавать в модель данные в нужном ей виде
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

C:\Users\robst\anaconda3\envs\gpt2\lib\site-packages\transformers\data\datasets\language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [25]:
%pip install transformers[torch]

                                              0.0/227.6 kB ? eta -:--:--
     -----                                    30.7/227.6 kB ? eta -:--:--
     ------------------                     112.6/227.6 kB 1.7 MB/s eta 0:00:01
     -------------------------------------- 227.6/227.6 kB 1.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [8]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir= "./finetuned",
    overwrite_output_dir=True,
    num_train_epochs=100,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,
    gradient_accumulation_steps=16,
    )


trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    optimizers = (torch.optim.AdamW(model.parameters(),lr=1e-5),None) # Optimizer and lr scheduler
)

In [9]:
trainer.train()

{'loss': 3.6004, 'learning_rate': 7.916666666666667e-06, 'epoch': 20.62}
{'loss': 3.2936, 'learning_rate': 5.833333333333334e-06, 'epoch': 41.24}
{'loss': 3.1139, 'learning_rate': 3.7500000000000005e-06, 'epoch': 61.86}
{'loss': 3.0048, 'learning_rate': 1.6666666666666667e-06, 'epoch': 82.47}
{'train_runtime': 7753.2815, 'train_samples_per_second': 159.816, 'train_steps_per_second': 0.31, 'train_loss': 3.2041277058919273, 'epoch': 98.97}


TrainOutput(global_step=2400, training_loss=3.2041277058919273, metrics={'train_runtime': 7753.2815, 'train_samples_per_second': 159.816, 'train_steps_per_second': 0.31, 'train_loss': 3.2041277058919273, 'epoch': 98.97})

In [10]:
text = "Дождь идет "
input_ids = tokenizer.encode(text, return_tensors="pt").to(DEVICE)
model.eval()
with torch.no_grad():
    out = model.generate(input_ids,
                        do_sample=True,
                        num_beams=5, top_k=50,
                        max_length=300,
                        repetition_penalty=3.5
                        )

generated_text = list(map(tokenizer.decode, out))[0]
print()
print(generated_text)


Дождь идет???

Да нет, не может быть и в помине.

А что же это за дождь такой?

И почему его так сильно жжет?

Наверно из-за того, что он очень холодный.

Может быть дело в том, что этот дождь как-то связан с погодой?

Ну да, а что же это за дождь такой?

Что же это за дождь такой?

Этот дождь...





Чайный пьяница! Чайный пьяница!

Твой чайный пьяница! Мой чайный пьяница!

Мой чайный пьяница!

Шанхайский пьяница!

Наш чайный пьяница! Шанхайский пьяница!

Сделай глубокий вдох - почувствуй бодрящий смоук!

Попробуй сделать глубокий вдох - почувствуй бодрящий смоук!

Мы приглашаем тебя на чайный праздник!

Вдоль по Новорижскому шоссе до Китай-города,

Посмотреть на Москву-реку со стороны Байконура.

Охуенный чайный пьяница!

Мутный чайный пьяница!

Лягушачий пьяница!

Холодный чайный пьяница!

Бодрый чайный пьяница! Бодрящий чайный пьяница!


In [15]:
text = "Жаба плачет "
input_ids = tokenizer.encode(text, return_tensors="pt").to(DEVICE)
model.eval()
with torch.no_grad():
    out = model.generate(input_ids,
                        do_sample=True,
                        num_beams=5, top_k=50,
                        max_length=300,
                        repetition_penalty=3.5
                        )

generated_text = list(map(tokenizer.decode, out))[0]
print()
print(generated_text)


Жаба плачет???

Я не в обиде, я просто хочу чтоб ты знала.

Прости меня пожалуйста за то что наговорила лишнего,

Но мне так хочется быть с тобой хоть чуть-чуть счастливыми.

Ведь это так просто - влюбиться без памяти раз и навсегда.

И всё будет хорошо, ну а пока...





Дождь льёт как из ведра

По тротуарам тает снег

Снег убирают бульдозеры

Всюду грязь вперемешку с мелким гравием

Улицы превращаются в лабиринт дворов

Туда где нет парковочных мест

Где пешеходы переходят проезжую часть на зеленый сигнал светофора

Раньше здесь было много машин

Теперь же их стало намного больше

Грязная жижа стекает по бордюрам

Заправка превратилась в грязную лужу

На улицах бродят голодные псы

Они жрут друг друга словно бездомные псы

Ненавистные взгляды прохожих

Ходят слухи о том, что кто-то кого-то съебал

Люди теряют разум

Кто-то теряет рассудок

А кто-то уже бежит куда глаза глядят

К чёрту все эти сплетни

Местные жители ведут себя крайне странно

Остаётся лишь гадать

Куда они подевалис

In [18]:
text = "Все пройдет "
input_ids = tokenizer.encode(text, return_tensors="pt").to(DEVICE)
model.eval()
with torch.no_grad():
    out = model.generate(input_ids,
                        do_sample=True,
                        num_beams=8, top_k=100,
                        max_length=500,
                        repetition_penalty=5.0
                        )

generated_text = list(map(tokenizer.decode, out))[0]
print()
print(generated_text)


Все пройдет???

Я не знаю, может быть это и странно, но я как-то по-другому смотрю на вещи.

И если честно, то мне кажется, что в этом мире все еще есть место для чего-то большего.

Мне так хочется верить в лучшее...





Меня зовут Саша, а тебя Оля?

Слышь, давай без глупостей, ладно?

У меня к тебе одна просьба:

Не подходи ко мне с вопросами типа "Как дела?"

Давай лучше поговорим о чем-нибудь серьезном!

Ты же знаешь, у меня всегда было много девушек,

Но почему-то они казались мне какими-то грустными.

А тут вдруг такая удача - встретил ты свою вторую половинку!

Наверно судьба свела нас вместе таким вот странным путем.

Такое чувство, будто кто-то специально кого-то подкарауливает,

Хочет завладеть твоим вниманием.

Пытается проникнуть в самое твое сердце,

В самые потаенные уголки твоей души.

Кому-то нужен только секс, кому-то деньги, кому-то работа,

Кто-то просто хочет почувствовать себя звездой.

Что бы ни происходило между нами, мы остаемся прежними,

Мы словно два разных 

In [11]:
text = "Дождь идет "
input_ids = tokenizer.encode(text, return_tensors="pt").to(DEVICE)
model.eval()
with torch.no_grad():
    out = model.generate(input_ids,
                        do_sample=True,
                        num_beams=5, top_k=100,
                        max_length=300,
                        repetition_penalty=3.5,
                        no_repeat_ngram_size=2,
                        )

generated_text = list(map(tokenizer.decode, out))[0]
print()
print(generated_text)


Дождь идет???

Нет, это не дождь, а скорее ливень. А что же это такое? И куда же подевались все мои мысли? Где мой дом? Что с нами стало? С кем мне теперь делить свои радости и горести? Кто научил меня жить по-другому? Может быть, я сам стал причиной этих несчастий? Быть может, виной всему то, что со мною произошло? Возможно, причина всего лишь во мне самом? Да, да, именно так! Но разве можно обвинять кого-то другого? Нет, конечно, нет! Разве можно судить о людях по их поступкам? Ведь у каждого из нас есть выбор - либо идти до конца, либо оказаться в руках палача. Я вижу свет в конце тоннеля, но пока он горит, остается надежда на чудо.
В душе моей тает искра надежды, как свеча в горящей лампе. Надежда умирает последней, она сгорает вместе с прошлым...
Я прошу тебя только об одном: дай мне сил сделать еще один шаг навстречу свету. Дай мне веру в тех, кто любит меня таким, какой я есть. Помоги мне стать тем, кому я буду верен. Позволь мне верить в чудеса. Верить в лучшее. Верь в себя. Н

In [14]:
for temp in [0.001, 0.1, 0.2, 0.5, 0.7, 1., 5.]:

    out = model.generate(input_ids, do_sample=True,
                     top_k=0,
                     temperature=temp,
                     max_length=50)


    generated_text = list(map(tokenizer.decode, out))[0]
    print("### text with temp - ", temp)
    print(generated_text)
    print()

### text with temp -  0.001
Дождь идет???





Я не знаю, что это такое, но я не знаю, что это такое

Я не знаю, что это такое, но я не знаю, что это такое

Я не знаю

### text with temp -  0.1
Дождь идет???





Я не знаю, что это такое, но я не знаю, что это такое

Я не знаю, что это такое, но я не знаю, что это такое

Я не знаю

### text with temp -  0.2
Дождь идет???





Я не знаю, что будет завтра,

Но я точно знаю, что будет завтра,

Я знаю, что будет завтра,

Я знаю, что будет завтра,



### text with temp -  0.5
Дождь идет???





У меня есть подруга, у неё есть айфон,

У неё есть подруга, у неё есть айфон,

У неё есть подруга, у неё есть айфон,



### text with temp -  0.7
Дождь идет 
Улицы ведут к храму, там в храме ждет меня

Смотрю в глаза, в них огонь я чувствую

И я не хочу умирать, иначе буду жить

Я не хочу умирать, ведь на

### text with temp -  1.0
Дождь идет????? Удиви меня

Ты? Это кто? И за что ты сама, а?

Меняет ход истории, меняет эпоху

Переделывает предками с

### Задание  2 (2 балла)

Ответьте на следующие вопросы:

1) В каких статьях были представлены GPT-1, GPT-2, GPT-3?
    https://cdn.openai.com/research-covers/language-unsupervised/language_understanding_paper.pdf
    https://cdn.openai.com/better-language-models/language_models_are_unsupervised_multitask_learners.pdf
    https://arxiv.org/abs/2005.14165
2) Как собирался обучающий корпус для GPT-3? Каким образом создатели старались обеспечить высокое качество текстов в обучающей выборке?
    Common Crawl(2016-2019) (почти триллион слов) + Books1 + Books2 + EN wikipedia.
    1) Фильтрация CC на основе сходства с высококачественными эталонными корпусами. (45тб -> 570гб)
    2) Нечеткая дедупликация на уровне документа, внутри и между наборами данных, для предотвращения избыточности и сохранения целостности отложенного валидационного набора как точного показателя переобучения.